In [61]:
import os
import torch
import pickle
from tqdm import *
import numpy as np
import pandas as pd
from PIL import Image
import cn_clip.clip as clip
from eval_recall import get_performance
from utils.config import get_config
from cn_clip.clip import load_from_name, available_models
from utils.utils import set_seed
from time import time


class Raw2Vector:
    def __init__(self, image_model, text_model, args):
        self.args = args
        print("Available models:", available_models())
        # Available models: ['ViT-B-16', 'ViT-L-14', 'ViT-L-14-336', 'ViT-H-14', 'RN50']
        device = "cuda" if torch.cuda.is_available() else "cpu"
        self.model, self.preprocess = load_from_name("ViT-B-16", device=device, download_root='../BigDataSource/')
        self.model.eval()

    def image2tensor(self, image):
        image = image.unsqueeze(0).to(self.args.device)
        with torch.no_grad():
            image_features = self.model.encode_image(image)
            image_features /= image_features.norm(dim=-1, keepdim=True)
        return image_features

    def text2tensor(self, text):
        # text = text.unsqueeze(0).to(self.args.device)
        with torch.no_grad():
            text_features = self.model.encode_text(text)
            text_features /= text_features.norm(dim=-1, keepdim=True)
        return text_features

    def retrieve(self, query, database):
        # query = query.unsqueeze(0).to(self.args.device)
        query, database = query.to('mps'), database.to('mps')
        logit_scale = self.model.logit_scale.exp().to('mps')
        logits_per_query = logit_scale * query @ database.t()
        probs = logits_per_query.softmax(dim=-1).cpu().detach().numpy()
        return probs

def get_all_image():
    # 本地化保存
    try:
        with open('../BigDataSource/Teddy2024/附件1/image_features_cpu.pkl', 'rb') as f:
            all_image_features = pickle.load(f)
            # torch.load(f, map_location='cpu')
    except:
        # 获得附件1数据集代码
        all_image = os.listdir('../BigDataSource/Teddy2024/附件1/ImageData')

        # 获得预训练模型
        transfer = Raw2Vector('ViT-B-16', '1', args)

        # 准备用多线程代码迅速获得所有图像的张量
        from concurrent.futures import ThreadPoolExecutor, as_completed
        def function(inputs):
            image_name = inputs
            image_address = '../BigDataSource/Teddy2024/附件1/ImageData/'
            file_name = image_address + image_name
            raw_image = Image.open(file_name)
            image_tensor = transfer.preprocess(raw_image)
            image_features = transfer.image2tensor(image_tensor)
            return image_name, image_features

        input_list = [image_name for image_name in all_image]
        all_image_features = []
        with ThreadPoolExecutor(max_workers=16) as executor:
            futures = [executor.submit(function, inputs) for inputs in input_list]
            for future in tqdm(as_completed(futures), total=len(all_image)):
                image_name, image_features = future.result()
                all_image_features.append([image_name, image_features])
        with open('../BigDataSource/Teddy2024/附件1/image_features_cpu.pkl', 'wb') as f:
            pickle.dump(all_image_features, f)
        print('图像数据预训练并存储完毕!')
    return all_image_features

def get_all_text():
    # 本地化保存
    try:
        with open('../BigDataSource/Teddy2024/附件1/text_features_cpu.pkl', 'rb') as f:
            all_text_features = pickle.load(f)
    except:
        # 获得附件1数据集代码
        all_text = pd.read_csv('../BigDataSource/Teddy2024/附件1/ImageWordData.csv').to_numpy()[:, 1]

        # 获得预训练模型
        transfer = Raw2Vector('ViT-B-16', '1', args)

        # 准备用多线程代码迅速获得所有文本的张量
        from concurrent.futures import ThreadPoolExecutor, as_completed
        def function(inputs):
            raw_text = inputs
            text_tensor = clip.tokenize(raw_text).to(args.device)
            text_features = transfer.text2tensor(text_tensor)
            return raw_text, text_features

        input_list = [raw_text for raw_text in all_text]
        all_text_features = []
        with ThreadPoolExecutor(max_workers=16) as executor:
            futures = [executor.submit(function, inputs) for inputs in input_list]
            for future in tqdm(as_completed(futures), total=len(all_text)):
                raw_text, text_features = future.result()
                all_text_features.append([raw_text, text_features])
        with open('../BigDataSource/Teddy2024/附件1/text_features_cpu.pkl', 'wb') as f:
            pickle.dump(all_text_features, f)
        print('文本数据预训练并存储完毕!')
    return all_text_features


def numpy_top_k_indices(matrix, k, axis=1):
    if axis == 1:  # 处理每行
        k = min(k, matrix.shape[1])
        indices = np.argsort(matrix, axis=1)[:, -k:][:, ::-1]
    elif axis == 0:  # 处理每列
        k = min(k, matrix.shape[0])
        indices = np.argsort(matrix, axis=0)[-k:, :][::-1, :]
    return indices

def high_speed_retreive(database, query, model, k):
    # Group truth 自己检索自己，除了自己以外的排名，故 + 1
    from modules.models.Retrieve import LSH, L2Index
    d = 512  # 向量维度
    if model == 'L2':
        print('执行L2检索部分')
        t1 = time()
        l2index = L2Index(k=k, d=d)
        topk_distence, topk_indices = l2index.search_topk_embeds(database, query)
        t2 = time()
        print(f'L2: {t2 - t1 : .2f}s')
    elif model == 'KNN':
        print('执行KNN检索部分')
        probs = transfer.retrieve(database, query)
        t1 = time()
        topk_indices = numpy_top_k_indices(probs, k, 1)
        t2 = time()
        print(f'KNN: {t2 - t1 : .2f}s')
    elif model == 'LSH':
        print('执行LSH检索部分')
        t1 = time()
        lsh = LSH(k=k, d=d, nbits=4)
        topk_distence, topk_indices = lsh.search_topk_embeds(database, query)
        t2 = time()
        print(f'LSH: {t2 - t1 : .2f}s')
    return topk_indices


In [20]:
args = get_config()
set_seed(2024)
data = pd.read_csv('../BigDataSource/Teddy2024/附件1/ImageWordData.csv').to_numpy()
transfer = Raw2Vector('ViT-B-16', '1', args)

# 首先获得所有的特征
all_image_features = get_all_image()
all_text_features = get_all_text()

# 修正序号
try:
    with open('../BigDataSource/Teddy2024/附件1/image_features_final.pkl', 'rb') as f:
        all_image_features = pickle.load(f)
    with open('../BigDataSource/Teddy2024/附件1/text_features_final.pkl', 'rb') as f:
        all_text_features = pickle.load(f)
except:
    all_image_idx = []
    all_text_idx = []
    for i in range(len(all_text_features)):
        all_image_idx.append(all_image_features[i][0])
        all_text_idx.append(all_text_features[i][0])
    new_image_features = []
    new_text_features = []
    for i in trange(len(data)):
        image_idx = all_image_idx.index(data[i][0])
        text_idx = all_text_idx.index(data[i][1])
        new_image_features.append([data[i][0], data[i][1], all_image_features[image_idx][1]])
        new_text_features.append([data[i][0], data[i][1], all_text_features[text_idx][1]])

    all_image_features = new_image_features
    all_text_features = new_text_features
    with open('../BigDataSource/Teddy2024/附件1/image_features_final.pkl', 'wb') as f:
        pickle.dump(all_image_features, f)
    with open('../BigDataSource/Teddy2024/附件1/text_features_final.pkl', 'wb') as f:
        pickle.dump(all_text_features, f)

# 直接获取张量
image_features = []
for i in range(len(all_image_features)):
    image_features.append(all_image_features[i][2])
image_features = torch.stack(image_features).squeeze(1)
print(image_features.shape)
print(all_image_features[0][0])
text_features = []
for i in range(len(all_text_features)):
    text_features.append(all_text_features[i][2])
text_features = torch.stack(text_features).squeeze(1)
print(text_features.shape)
print(all_text_features[0][1])

{'experiment': 'Run the experiment now!'}
Available models: ['ViT-B-16', 'ViT-L-14', 'ViT-L-14-336', 'ViT-H-14', 'RN50']
Loading vision model config from /Users/zengyuxiang/Documents/科研代码/CLIP_finetune/cn_clip/clip/model_configs/ViT-B-16.json
Loading text model config from /Users/zengyuxiang/Documents/科研代码/CLIP_finetune/cn_clip/clip/model_configs/RoBERTa-wwm-ext-base-chinese.json
Model info {'embed_dim': 512, 'image_resolution': 224, 'vision_layers': 12, 'vision_width': 768, 'vision_patch_size': 16, 'vocab_size': 21128, 'text_attention_probs_dropout_prob': 0.1, 'text_hidden_act': 'gelu', 'text_hidden_dropout_prob': 0.1, 'text_hidden_size': 768, 'text_initializer_range': 0.02, 'text_intermediate_size': 3072, 'text_max_position_embeddings': 512, 'text_num_attention_heads': 12, 'text_num_hidden_layers': 12, 'text_type_vocab_size': 2}
torch.Size([50000, 512])
Image14001001-0000.jpg
torch.Size([50000, 512])
《绿色北京》摄影大赛胡子<人名>作品


In [21]:
all_pred_rank = high_speed_retreive(image_features, text_features, 'L2', 1000)
ans = []
for i in range(len(all_pred_rank)):
    print('-' * 80)
    print(all_image_features[i][0], all_image_features[i][1])
    for j in range(len(all_pred_rank[i])):
        print(all_text_features[all_pred_rank[i][j]][1])
    # break
    if i >= 30:
        break

执行L2检索部分
L2:  20.60s
--------------------------------------------------------------------------------
Image14001001-0000.jpg 《绿色北京》摄影大赛胡子<人名>作品
未必柳条能蘸水,水中柳影引他长. 春柳 嫩色含轻雨,柔丝弄早春.
北京!"中国历史上第一城市快速路"环三环超级马拉松
宿根园中赏花卉且向心中觅辶挂
堤岸翠绿,泄洪畅通,环境幽雅,旅游资源丰富,成为一条亮丽的风景线
天津市滨海新区东半圆路靠近中国农业银行(上海道支行
在这里,我衷心希望各位学弟学妹也能考取自己喜欢的学校,取得进步!
盼兮 暮兮 往兮 归兮只愿你一切安好-白雅
复赛将采取摄影家投票 现场投票的方式,摄影家票数与现场顾客投票票
随着时间的推移,知道这个地儿的人一定会越来越多,景色是否依旧会
nokia 诺基亚 lumia 1020智能手机-实拍-故宫角楼
换句话说就是七星漂在作钓时如何配重,也就是如何调漂.
这里市井生活味和人情味更浓郁,让人无法忘怀.
春天慢慢的走过来了, 让我们享受温暖的阳光, 也让大地充满快乐的
牡丹江生态公园之文化主题公园设计方案
在追求幸福美好生活的新时代下,城建园林将紧随国家生态文明建设的
运动没有那么多限制,来曲江一起"动起来"!
"全省旅发大会"能给大庆带来什么
图中这种金龟子喜欢呆在一种果实类似杨梅的树上,果实成熟时比杨梅更
北京将综合治理杨柳雌株30万棵 杨柳树不能"一砍了之"
人无完人看淡一点开心多一点抬起头低下心踏实做事简单做人
与恐龙同时代被称水中捕蝇草珍稀濒危物种再现龙江湿地
[北京ing]"十三五"末城市副中心绿色出行比例将达80%
【101巨邀约】太撩人:2017仙居绿道马拉松即将开赛!
北湖公园,面积超大,湖面波光粼粼,岸上杨柳泛青,还有鲜花盛开.
有购在昆区,住在青山,吃在东河之说.
带你在线"云游" 赏秋日最美凤湖_疫情
初夏,在这杨絮纷飞的季节,到处弥漫着温暖的气息.
春夜一起漫步什刹海
清凌凌的水,<人名>的天,在群山之间相映成趣.
健康第一,不要太操劳,保重身体.
据中原地产研究中心的统计数据显示:北京7月全月累计二手房住宅签约
是如何做到长盛不衰源远流长的.
————学拍剪影效果和夕阳余晖之"紫禁城角楼"!——


In [56]:
all_real_rank = high_speed_retreive(text_features, text_features, 'L2', 1000)
ans = []
for i in range(len(all_pred_rank)):
    print('-' * 80)
    print(all_text_features[i][0], end='  ')
    for j in range(len(all_real_rank[i])):
        print(all_text_features[all_real_rank[i][j]][1])
    # break
    if i >= 30:
        break

执行L2检索部分
L2:  10.56s
--------------------------------------------------------------------------------
Image14001001-0000.jpg  《绿色北京》摄影大赛胡子<人名>作品
摄影师赵勇鹤 的作品主题分为两大类 一是居住二十多年的北京,一是
王东 摄影
谢析搏摄影
老铁们,北京已经成为全国最最最最美的城市!
薛航/摄03|"一起来拍个照吧!
拍摄自然,这才正符合自然法则,自然之道.
6月影赛"人文小品"类作品征集------依偎
中国摄影家协会会员,广东省摄影家协会理事,深圳九月艺术空间创办人
当然,这还只是植物园春花的前奏曲,在这里能够真切地体验北京春天的
成都摄影·官方群
文旅融合,顺义打造国际旅游目的地
长焦dc题材拍摄样片赏
一方水土养一方人,也孕育一方文化,一座城最能打动人的地方
京中铭记-奥林匹克公园&森林公园
"自然的力量"摄影大赛获奖作品欣赏
" 是的,美景在身边,珍惜常在 这就是生活实实在在的幸福感
一份建议催生一张城市新名片
罗缙人文纪实摄影诗作《追》
在追求幸福美好生活的新时代下,城建园林将紧随国家生态文明建设的
认识一位风光摄影大师,他一直坚持拍反转片,他的作品没有太多的
探寻老北京的味道
越来越多的摄影爱好者,已经不满足于在摄影棚里拍摄一些枯燥单调的
新唐山,新城市,新风采
北京疏解加速,北三县的天时
小伙伴们,我们在北京等你,加入我们,一起干番大事业!
那些光影记录下的故事
那么,开启亲近唐山的新方式入夜后,晚风轻抚,霓虹闪烁<人名>气有些
摄影_
野活泼物摄影师若何捕获到一个无机的生态体系?
这里有湖泊湿地,有森林草甸,有河谷溪流,还有珍稀动植物.
这里有壮丽奇异的自然资源,容近朴归真古代文明和原始生态无穷魅力的
随着北京旧城旧房的改造,其价格不断的攀升.
绝对原创无题七绝
北京辖区上市公司有着举足轻重的地位,在资本市场中发挥着不可替代的
而共青团北京市委机关报北京青年报,则在头版底部刊发配图简讯及
在北大和春天约会一场
北京!"中国历史上第一城市快速路"环三环超级马拉松
史风——江城东湖的眼眸!
34平方米,建成区绿地率为41.03%,森林覆盖率达52.
复赛将采取摄影家投票 现场投票的方式,摄影家票数与现场顾客投票票
回

In [62]:
all_pred_rank = high_speed_retreive(image_features, text_features, 'KNN', 1000)
ans = []
for i in range(len(all_pred_rank)):
    print('-' * 80)
    print(all_image_features[i][0], all_image_features[i][1])
    for j in range(len(all_pred_rank[i])):
        print(all_text_features[all_pred_rank[i][j]][1])
    # break
    if i >= 30:
        break

执行KNN检索部分
KNN:  40.95s
--------------------------------------------------------------------------------
Image14001001-0000.jpg 《绿色北京》摄影大赛胡子<人名>作品
扬中是一座集港口,工贸,旅游且适宜人居和创业的江南新兴城市.
07年9号线松江新城至桂林路通车,17年三期曹路通车!
亚博光影    10 漂亮作品! 夏之夜    10 相当给力!
松江哪条路的名字最好听?
便捷的交通使得新区科技成为苏州高知人群的绿色居住前沿特区
创新引领-科技强区
"中国制造业第一县"改革发展风正劲|四十不惑,江阴
嘉兴市嘉善县姚庄镇桃源新邨社区.
由锡山经济开发区管委会负责开发建设,重点发展高新技术产业
未来十年,4大要素带动嘉兴科技城,助力长三角发展!
景源名墅位于奉贤南桥城西生活核心区,14万平方米的加州国际社区.
大美盐城——湿地篇
青浦热门游记,青浦自助游游记,青浦旅游热门游记 - 马
水漾的江都
成长历程_苏州神州数码捷通科技有限公司
春风杨柳 再游如东
新唐山,新城市,新风采
新园区网致力打造成为--全球园区领域综合服务商
住在龙城
我的500d育成纪录---完结篇
【醉美夜空】----喜迎apec
长焦dc题材拍摄样片赏
自2018年5号线南延伸段通车后,奉贤更是进入了地铁时代.
中国哪座城市房地产最值得投资? 【猫眼看人】-凯迪
扬州人,你为什么要在西区买房!
这张1600×1200的&nbsp;不知可否满意
夜间卫星图可以从侧面反映出一个地方的经济发展水平,城建规模和水平
在东台串场河成为风光无限的自然景区
绿城中国
邻里邻外
未来的嘉善不再是只有一个选择,老城因为本身具备的人口基数和城市
5d2 24-70周庄行
鑫苑国际城市花园昆山市
现代服务业和居住生活为主的城市综合功能区
据统计,2013年崇贤国有建设用地计划指标为202.
碧桂园蔚蓝距沪苏杭均在一小.时车程,地理位置十分优越.
证大家园
卓成动态,卓成网络科技,张家港网站建设领导者-400
6月70城二手房价涨幅收窄 上海最贵小区27万/平
科学规划停车位,改造修补破损道路;综合整治南湾浜,龙士井黑臭河道
东部新城 宁波国际航运产业集聚区
浦东创评全国文明城区,祝桥时刻准备着


In [66]:
all_real_rank.shape

(50000, 100)

In [67]:
all_pred_rank.shape

(50000, 1000)

In [68]:
import numpy as np

def recall_at_k(relevant, recommended, k):
    """
    计算 Recall@K
    :param relevant: 实际感兴趣的项目矩阵，每行代表一个用户的相关项目集合，二维数组
    :param recommended: 推荐系统给出的推荐项目矩阵，每行代表一个用户的推荐项目列表，二维数组
    :param k: 考虑的推荐列表的前K项
    :return: 每个用户的 Recall@K 的值，一维数组
    """
    recalls = []
    for rel_set, rec_list in zip(relevant, recommended):
        if k < len(rec_list):
            rec_list_k = rec_list[:k]
        else:
            rec_list_k = rec_list
        relevant_recommended = set(rel_set).intersection(rec_list_k)
        if len(rel_set) > 0:
            recalls.append(len(relevant_recommended) / len(set(rel_set)))
        else:
            recalls.append(0)
    return np.array(recalls)

def dcg_at_k(scores, k):
    """
    计算 DCG@K
    :param scores: 相关性得分列表，列表类型
    :param k: 考虑的推荐列表的前K项
    :return: DCG@K 的值
    """
    scores = scores[:k]
    if len(scores):
        return np.sum(scores / np.log2(np.arange(2, len(scores) + 2)))  # log base 2 of positions 2 through k+1
    return 0

def ndcg_at_k(relevant, recommended, k):
    """
    计算 NDCG@K
    :param relevant: 实际感兴趣的项目矩阵，二维数组
    :param recommended: 推荐项目矩阵，二维数组
    :param k: 考虑的推荐列表的前K项
    :return: 每个用户的 NDCG@K 的值，一维数组
    """
    ndcgs = []
    for rel_set, rec_list in zip(relevant, recommended):
        rel_set = set(rel_set)
        if k < len(rec_list):
            rec_list_k = rec_list[:k]
        else:
            rec_list_k = rec_list
        
        actual_scores = [1 if item in rel_set else 0 for item in rec_list_k]
        ideal_scores = [1] * min(len(rel_set), k)
        
        actual_dcg = dcg_at_k(actual_scores, k)
        ideal_dcg = dcg_at_k(ideal_scores, k)
        
        if ideal_dcg > 0:
            ndcgs.append(actual_dcg / ideal_dcg)
        else:
            ndcgs.append(0)
    return np.array(ndcgs)

def get_performance(relevant, recommended, k_value):
    # 计算 Recall@K 和 NDCG@K
    recalls = recall_at_k(relevant, recommended, k_value)
    ndcgs = ndcg_at_k(relevant, recommended, k_value)
    return {
        'recalls' : recalls,
        'ndcgs' : ndcgs
    }

# for i in range(len(all_pred_rank)):
#     print(all_real_rank[i].shape, all_pred_rank[i].shape)
for k in [5, 10, 20, 50]:
    results = get_performance(all_real_rank, all_pred_rank, k)
    string = f"Recall@{k}="
    print(f"{string:15s}{results['recalls'].mean():.4f}")
    string = f"NDCG@{k}="
    print(f"{string:15s}{results['ndcgs'].mean():.4f}")

Recall@5=      0.0030
NDCG@5=        0.0615
Recall@10=     0.0056
NDCG@10=       0.0581
Recall@20=     0.0101
NDCG@20=       0.0535
Recall@50=     0.0211
NDCG@50=       0.0460
